# Evaluate prediction metrics 
- This notebook is used to check out each of our storm impact prediction models performed in comparison to our observed storm impacts.

## Setup notebook
Import our required packages and set default plotting options.

In [ ]:
# Enable autoreloading of our modules. 
# Most of the code will be located in the /src/ folder, 
# and then called from the notebook.
%matplotlib inline
%reload_ext autoreload
%autoreload

In [ ]:
from IPython.core.debugger import set_trace

import pandas as pd
import numpy as np
import os
import decimal
import plotly
import plotly.graph_objs as go
import plotly.plotly as py
import plotly.tools as tls
import plotly.figure_factory as ff
from plotly import tools
import plotly.io as pio
from scipy import stats
import math
import matplotlib
from matplotlib import cm
import colorlover as cl
from tqdm import tqdm_notebook
from ipywidgets import widgets, Output
from IPython.display import display, clear_output, Image, HTML
from scipy import stats
from sklearn.metrics import confusion_matrix, matthews_corrcoef
import matplotlib.pyplot as plt
from matplotlib.ticker import MultipleLocator
from matplotlib.lines import Line2D
from cycler import cycler
from scipy.interpolate import interp1d
from pandas.api.types import CategoricalDtype

In [ ]:
# Matplot lib default settings
plt.rcParams["figure.figsize"] = (10,6)
plt.rcParams['axes.grid']=True
plt.rcParams['grid.alpha'] = 0.5
plt.rcParams['grid.color'] = "grey"
plt.rcParams['grid.linestyle'] = "--"
plt.rcParams['axes.grid']=True

# https://stackoverflow.com/a/20709149
matplotlib.rcParams['text.usetex'] = True

matplotlib.rcParams['text.latex.preamble'] = [
       r'\usepackage{siunitx}',   # i need upright \micro symbols, but you need...
       r'\sisetup{detect-all}',   # ...this to force siunitx to actually use your fonts
       r'\usepackage{helvet}',    # set the normal font here
       r'\usepackage{amsmath}',
       r'\usepackage{sansmath}',  # load up the sansmath so that math -> helvet
       r'\sansmath',              # <- tricky! -- gotta actually tell tex to use!
]  

## Import data
Import our data from the `./data/interim/` folder and load it into pandas dataframes. 

In [ ]:
def df_from_csv(csv, index_col, data_folder='../data/interim'):
    print('Importing {}'.format(csv))
    return pd.read_csv(os.path.join(data_folder,csv), index_col=index_col)

df_waves = df_from_csv('waves.csv', index_col=[0, 1])
df_tides = df_from_csv('tides.csv', index_col=[0, 1])
df_profiles = df_from_csv('profiles.csv', index_col=[0, 1, 2])
df_sites = df_from_csv('sites.csv', index_col=[0])
df_sites_waves = df_from_csv('sites_waves.csv', index_col=[0])
df_profile_features_crest_toes = df_from_csv('profile_features_crest_toes.csv', index_col=[0,1])

# Note that the forecasted data sets should be in the same order for impacts and twls
impacts = {
    'forecasted': {
    'postintertidal_slope_hol86': df_from_csv('impacts_forecasted_postintertidal_slope_hol86.csv', index_col=[0]),
    'postintertidal_slope_nie91': df_from_csv('impacts_forecasted_postintertidal_slope_nie91.csv', index_col=[0]),
    'postintertidal_slope_pow18': df_from_csv('impacts_forecasted_postintertidal_slope_pow18.csv', index_col=[0]),
    'postintertidal_slope_sto06': df_from_csv('impacts_forecasted_postintertidal_slope_sto06.csv', index_col=[0]),
    'postmean_slope_hol86': df_from_csv('impacts_forecasted_postmean_slope_hol86.csv', index_col=[0]),
    'postmean_slope_nie91': df_from_csv('impacts_forecasted_postmean_slope_nie91.csv', index_col=[0]),
    'postmean_slope_pow18': df_from_csv('impacts_forecasted_postmean_slope_pow18.csv', index_col=[0]),
    'postmean_slope_sto06': df_from_csv('impacts_forecasted_postmean_slope_sto06.csv', index_col=[0]),
    'preintertidal_slope_hol86': df_from_csv('impacts_forecasted_preintertidal_slope_hol86.csv', index_col=[0]),
    'preintertidal_slope_nie91': df_from_csv('impacts_forecasted_preintertidal_slope_nie91.csv', index_col=[0]),
    'preintertidal_slope_pow18': df_from_csv('impacts_forecasted_preintertidal_slope_pow18.csv', index_col=[0]),
    'preintertidal_slope_sto06': df_from_csv('impacts_forecasted_preintertidal_slope_sto06.csv', index_col=[0]),
    'premean_slope_hol86': df_from_csv('impacts_forecasted_premean_slope_hol86.csv', index_col=[0]),
    'premean_slope_nie91': df_from_csv('impacts_forecasted_premean_slope_nie91.csv', index_col=[0]),
    'premean_slope_pow18': df_from_csv('impacts_forecasted_premean_slope_pow18.csv', index_col=[0]),
    'premean_slope_sto06': df_from_csv('impacts_forecasted_premean_slope_sto06.csv', index_col=[0]),
        },
    'observed': df_from_csv('impacts_observed.csv', index_col=[0])
    }


twls = {
    'forecasted': {
    'postintertidal_slope_hol86': df_from_csv('twl_postintertidal_slope_hol86.csv', index_col=[0,1]),
    'postintertidal_slope_nie91': df_from_csv('twl_postintertidal_slope_nie91.csv', index_col=[0,1]),
    'postintertidal_slope_pow18': df_from_csv('twl_postintertidal_slope_pow18.csv', index_col=[0,1]),
    'postintertidal_slope_sto06': df_from_csv('twl_postintertidal_slope_sto06.csv', index_col=[0,1]),
    'postmean_slope_hol86': df_from_csv('twl_postmean_slope_hol86.csv', index_col=[0,1]),
    'postmean_slope_nie91': df_from_csv('twl_postmean_slope_nie91.csv', index_col=[0,1]),
    'postmean_slope_pow18': df_from_csv('twl_postmean_slope_pow18.csv', index_col=[0,1]),
    'postmean_slope_sto06': df_from_csv('twl_postmean_slope_sto06.csv', index_col=[0,1]),
    'preintertidal_slope_hol86': df_from_csv('twl_preintertidal_slope_hol86.csv', index_col=[0,1]),
    'preintertidal_slope_nie91': df_from_csv('twl_preintertidal_slope_nie91.csv', index_col=[0,1]),
    'preintertidal_slope_pow18': df_from_csv('twl_preintertidal_slope_pow18.csv', index_col=[0,1]),
    'preintertidal_slope_sto06': df_from_csv('twl_preintertidal_slope_sto06.csv', index_col=[0,1]),
    'premean_slope_hol86': df_from_csv('twl_premean_slope_hol86.csv', index_col=[0,1]),
    'premean_slope_nie91': df_from_csv('twl_premean_slope_nie91.csv', index_col=[0,1]),
    'premean_slope_pow18': df_from_csv('twl_premean_slope_pow18.csv', index_col=[0,1]),
    'premean_slope_sto06': df_from_csv('twl_premean_slope_sto06.csv', index_col=[0,1]),
    }
}
print('Done!')

## Generate longshore plots for each beach

In [ ]:
beaches = list(
    set([
        x[:-4] for x in df_profiles.index.get_level_values('site_id').unique()
    ]))

for beach in beaches:
   
    df_obs_impacts = impacts['observed'].loc[impacts['observed'].index.str.
                                             contains(beach)]

    # Get index for each site on the beach
    n = [x for x in range(len(df_obs_impacts))][::-1]
    n_sites = [x for x in df_obs_impacts.index][::-1]

    # Convert storm regimes to categorical datatype
    cat_type = CategoricalDtype(
        categories=['swash', 'collision', 'overwash', 'inundation'],
        ordered=True)
    df_obs_impacts.storm_regime = df_obs_impacts.storm_regime.astype(cat_type)

    # Create figure
    
    # Determine the height of the figure, based on the number of sites.
    fig_height = max(6, 0.18 * len(n_sites))
    f, (ax1, ax2, ax3, ax4, ax5, ax6, ax7, ax8, ax9) = plt.subplots(
        1,
        9,
        sharey=True,
        figsize=(18, fig_height),
        gridspec_kw={'width_ratios': [4, 4, 2, 2, 2, 2, 2, 2,2]})

    # ax1: Impacts

    # Define colors for storm regime
    cmap = {'swash': '#1a9850', 'collision': '#fee08b', 'overwash': '#d73027'}

    # Common marker style
    marker_style = {
        's': 60,
        'linewidths': 0.7,
        'alpha': 1,
        'edgecolors': 'k',
        'marker': 'o',
    }

    # Plot observed impacts
    colors = [cmap.get(x) for x in df_obs_impacts.storm_regime]
    colors = ['#aaaaaa' if c is None else c for c in colors]
    ax1.scatter([0 for x in n], n, color=colors, **marker_style)

    # Plot model impacts
    for i, model in enumerate(impacts['forecasted']):

        # Only get model results for this beach
        df_model = impacts['forecasted'][model].loc[
            impacts['forecasted'][model].index.str.contains(beach)]

        # Recast storm regimes as categorical data
        df_model.storm_regime = df_model.storm_regime.astype(cat_type)

        # Assign colors
        colors = [cmap.get(x) for x in df_model.storm_regime]
        colors = ['#aaaaaa' if c is None else c for c in colors]

        # Only plot markers which are different to the observed storm regime. 
        # This makes it easier to find where model predictions differ
        y_coords = []
        for obs_impact, for_impact in zip(df_model.storm_regime,
                                          df_obs_impacts.storm_regime):
            if obs_impact == for_impact:
                y_coords.append(None)
            else:
                y_coords.append(i + 1)

        ax1.scatter(y_coords, n, color=colors, **marker_style)

    # Add model names to each impact on x axis
    ax1.set_xticks(range(len(impacts['forecasted']) + 1))
    ax1.set_xticklabels(['observed'] +
                        [x.replace('_', '\_') for x in impacts['forecasted']])
    ax1.xaxis.set_tick_params(rotation=90)

    # Add title
    ax1.set_title('Storm regime')

    # Create custom legend
    legend_elements = [
        Line2D([0], [0],
               marker='o',
               color='w',
               label='Swash',
               markerfacecolor='#1a9850',
               markersize=8,
               markeredgewidth=1.0,
               markeredgecolor='k'),
        Line2D([0], [0],
               marker='o',
               color='w',
               label='Collision',
               markerfacecolor='#fee08b',
               markersize=8,
               markeredgewidth=1.0,
               markeredgecolor='k'),
        Line2D([0], [0],
               marker='o',
               color='w',
               label='Overwash',
               markerfacecolor='#d73027',
               markersize=8,
               markeredgewidth=1.0,
               markeredgecolor='k'),
    ]
    ax1.legend(
        handles=legend_elements, loc='lower center', bbox_to_anchor=(0.5, 1.1))

    # Replace axis ticks with names of site ids
    ytick_labels = ax1.get_yticks().tolist()
    yticks = [
        n_sites[int(y)] if all([y >= 0, y < len(n_sites)]) else ''
        for y in ytick_labels
    ]
    yticks = [x.replace('_', '\_') for x in yticks]
    ax1.set_yticklabels(yticks)

    # ax2: elevations

    # Dune elevations
    df_feats = df_profile_features_crest_toes.xs(['prestorm'],
                                                 level=['profile_type'])
    df_feats = df_feats.loc[df_feats.index.str.contains(beach)]

    ax2.plot(df_feats.dune_crest_z, n, color='#fdae61')
    ax2.plot(df_feats.dune_toe_z, n, color='#fdae61')
    ax2.fill_betweenx(
        n,
        df_feats.dune_toe_z,
        df_feats.dune_crest_z,
        alpha=0.2,
        color='#fdae61',
        label='$D_{low}$ to $D_{high}$')

    model_colors = [
        '#1f78b4',
        '#33a02c',
        '#e31a1c',
        '#6a3d9a',
        '#a6cee3',
        '#b2df8a',
        '#fb9a99',
        '#cab2d6',
        '#ffff99',
    ]

    # Define colors to cycle through for our R_high
    ax2.set_prop_cycle(cycler('color', model_colors))

    # For TWL elevations, Rhigh-Dlow and R2 axis, only plot a few models
    models_to_plot = [
        'premean_slope_hol86',
        'premean_slope_sto06',
        'preintertidal_slope_hol86',
        'preintertidal_slope_sto06',
    ]
    models_linewidth = 0.8

    # Plot R_high values
    for model in models_to_plot:

        # Only get model results for this beach
        df_model = impacts['forecasted'][model].loc[
            impacts['forecasted'][model].index.str.contains(beach)]

        # Recast storm regimes as categorical data
        ax2.plot(
            df_model.R_high,
            n,
            label=model.replace('_', '\_'),
            linewidth=models_linewidth)

    # Set title, legend and labels
    ax2.set_title('TWL \& dune\nelevations')
    ax2.legend(loc='lower center', bbox_to_anchor=(0.5, 1.1))
    ax2.set_xlabel('Elevation (m AHD)')
#     ax2.set_xlim([0, max(df_feats.dune_crest_z)])

    # ax3: Plot R_high - D_low

    # Define colors to cycle through for our R_high
    ax3.set_prop_cycle(cycler('color', model_colors))

    # Plot R_high values
    for model in models_to_plot:

        df_model = impacts['forecasted'][model].loc[
            impacts['forecasted'][model].index.str.contains(beach)]
        # R_high - D_low
        ax3.plot(
            df_model.R_high - df_feats.dune_toe_z,
            n,
            label=model.replace('_', '\_'),
            linewidth=models_linewidth)

    ax3.axvline(x=0, color='black', linestyle=':')
    ax3.set_title('$R_{high}$ - $D_{low}$')
    ax3.set_xlabel('Height (m)')
#     ax3.set_xlim([-2, 2])

    # Define colors to cycle through for our R2
    ax4.set_prop_cycle(cycler('color', model_colors))

    # R_high - D_low
    for model in models_to_plot:
        df_R2 = impacts['forecasted'][model].merge(
            twls['forecasted'][model], on=['site_id', 'datetime'], how='left')
        df_R2 = df_R2.loc[df_R2.index.str.contains(beach)]
        ax4.plot(
            df_R2.R2,
            n,
            label=model.replace('_', '\_'),
            linewidth=models_linewidth)

    ax4.set_title(r'$R_{2\%}$')
    ax4.set_xlabel('Height (m)')
#     ax4.set_xlim([0, 10])

    # Beach slope
    slope_colors = [
        '#bebada',
        '#bc80bd',
        '#ffed6f',
        '#fdb462',
    ]
    ax5.set_prop_cycle(cycler('color', slope_colors))
    slope_models = {
        'prestorm mean': 'premean_slope_sto06',
        'poststorm mean': 'postmean_slope_sto06',
        'prestorm intertidal': 'preintertidal_slope_sto06',
        'poststorm intertidal': 'postintertidal_slope_sto06',
    }

    for label in slope_models:
        model = slope_models[label]
        df_beta = impacts['forecasted'][model].merge(
            twls['forecasted'][model], on=['site_id', 'datetime'], how='left')
        df_beta = df_beta.loc[df_beta.index.str.contains(beach)]
        ax5.plot(df_beta.beta, n, label=label, linewidth=models_linewidth)

    ax5.set_title(r'$\beta$')
    ax5.set_xlabel('Beach slope')
    ax5.legend(loc='lower center', bbox_to_anchor=(0.5, 1.1))
    # ax5.set_xlim([0, 0.15])

    # Need to chose a model to extract environmental parameters at maximum R_high time
    model = 'premean_slope_sto06'
    df_beach = impacts['forecasted'][model].merge(
        twls['forecasted'][model], on=['site_id', 'datetime'], how='left')
    df_beach = df_beach.loc[df_beach.index.str.contains(beach)]

    # Wave height, wave period
    ax6.plot(df_beach.Hs0, n, color='#999999')
    ax6.set_title('$H_{s0}$')
    ax6.set_xlabel('Sig. wave height (m)')
    ax6.set_xlim([2, 6])

    ax7.plot(df_beach.Tp, n, color='#999999')
    ax7.set_title('$T_{p}$')
    ax7.set_xlabel('Peak wave period (s)')
    ax7.set_xlim([8, 14])

    ax8.plot(df_beach.tide, n, color='#999999')
    ax8.set_title('Tide \& surge')
    ax8.set_xlabel('Elevation (m AHD)')
    ax8.set_xlim([1, 3])

    
    # TODO Cumulative wave energy
    # df_sites_waves
    
    plt.tight_layout()
    f.subplots_adjust(top=0.88)
    f.suptitle(beach.replace('_', '\_'))

    # Set minor axis ticks on each plot
    ax1.yaxis.set_minor_locator(MultipleLocator(1))
    ax1.yaxis.grid(True, which='minor', linestyle='--', alpha=0.1)
    ax2.yaxis.grid(True, which='minor', linestyle='--', alpha=0.1)
    ax3.yaxis.grid(True, which='minor', linestyle='--', alpha=0.1)
    ax4.yaxis.grid(True, which='minor', linestyle='--', alpha=0.1)
    ax5.yaxis.grid(True, which='minor', linestyle='--', alpha=0.1)
    ax6.yaxis.grid(True, which='minor', linestyle='--', alpha=0.1)
    ax7.yaxis.grid(True, which='minor', linestyle='--', alpha=0.1)
    ax8.yaxis.grid(True, which='minor', linestyle='--', alpha=0.1)

    # # Print to figure
    plt.savefig('07_{}.png'.format(beach), dpi=600, bbox_inches='tight')

    plt.show()
    plt.close()
    print('Done: {}'.format(beach))
    
    break
print('Done!')

## Generate classification reports for each model
Use sklearn metrics to generate classification reports for each forecasting model.

In [ ]:
import sklearn.metrics

# Get observed impacts
df_obs = impacts['observed']

# Convert storm regimes to categorical datatype
cat_type = CategoricalDtype(
    categories=['swash', 'collision', 'overwash', 'inundation'], ordered=True)
df_obs.storm_regime = df_obs.storm_regime.astype(cat_type)

for model in impacts['forecasted']:
    df_for = impacts['forecasted'][model]
    df_for.storm_regime = df_for.storm_regime.astype(cat_type)

    m = sklearn.metrics.classification_report(
            df_obs.storm_regime.astype(cat_type).cat.codes.values,
            df_for.storm_regime.astype(cat_type).cat.codes.values,
            labels=[0, 1, 2, 3],
            target_names=['swash', 'collision', 'overwash', 'inundation'])
    print(model)
    print(m)
    print()
    

In [ ]:
# Check matthews coefficient
# https://scikit-learn.org/stable/modules/generated/sklearn.metrics.matthews_corrcoef.html

for model in impacts['forecasted']:
    df_for = impacts['forecasted'][model]
    df_for.storm_regime = df_for.storm_regime.astype(cat_type)

    m = matthews_corrcoef(
            df_obs.storm_regime.astype(cat_type).cat.codes.values,
            df_for.storm_regime.astype(cat_type).cat.codes.values)
    print('{}: {:.2f}'.format(model,m))

In [ ]:
# Check accuracy
# https://scikit-learn.org/stable/modules/generated/sklearn.metrics.matthews_corrcoef.html

for model in impacts['forecasted']:
    df_for = impacts['forecasted'][model]
    df_for.storm_regime = df_for.storm_regime.astype(cat_type)

    m = sklearn.metrics.accuracy_score(
            df_obs.storm_regime.astype(cat_type).cat.codes.values,
            df_for.storm_regime.astype(cat_type).cat.codes.values)
    print('{}: {:.2f}'.format(model,m))

In [ ]:
from sklearn.metrics import confusion_matrix
# Check confusion matrix
for model in impacts['forecasted']:
    df_for = impacts['forecasted'][model]
    df_for.storm_regime = df_for.storm_regime.astype(cat_type)

    m = sklearn.metrics.confusion_matrix(
            df_obs.storm_regime.astype(cat_type).cat.codes.values,
            df_for.storm_regime.astype(cat_type).cat.codes.values,
            labels=[0,1,2,3])
    print('{}\n{}'.format(model,m))

## Create confusion matrix figure
From https://github.com/wcipriano/pretty-print-confusion-matrix/blob/master/confusion_matrix_pretty_print.py

In [ ]:
# -*- coding: utf-8 -*-
"""
plot a pretty confusion matrix with seaborn
Created on Mon Jun 25 14:17:37 2018
@author: Wagner Cipriano - wagnerbhbr - gmail - CEFETMG / MMC
REFerences:
  https://www.mathworks.com/help/nnet/ref/plotconfusion.html
  https://stackoverflow.com/questions/28200786/how-to-plot-scikit-learn-classification-report
  https://stackoverflow.com/questions/5821125/how-to-plot-confusion-matrix-with-string-axis-rather-than-integer-in-python
  https://www.programcreek.com/python/example/96197/seaborn.heatmap
  https://stackoverflow.com/questions/19233771/sklearn-plot-confusion-matrix-with-labels/31720054
  http://scikit-learn.org/stable/auto_examples/model_selection/plot_confusion_matrix.html#sphx-glr-auto-examples-model-selection-plot-confusion-matrix-py
"""

#imports
from pandas import DataFrame
import numpy as np
import matplotlib.pyplot as plt
import matplotlib.font_manager as fm
from matplotlib.collections import QuadMesh
import seaborn as sn


def get_new_fig(fn, figsize=[9,9]):
    """ Init graphics """
    fig1 = plt.figure(fn, figsize)
    ax1 = fig1.gca()   #Get Current Axis
    ax1.cla() # clear existing plot
    return fig1, ax1
#

def configcell_text_and_colors(array_df, lin, col, oText, facecolors, posi, fz, fmt, show_null_values=0):
    """
      config cell text and colors
      and return text elements to add and to dell
      @TODO: use fmt
    """
    text_add = []; text_del = [];
    cell_val = array_df[lin][col]
    tot_all = array_df[-1][-1]
    per = (float(cell_val) / tot_all) * 100
    curr_column = array_df[:,col]
    ccl = len(curr_column)

    #last line  and/or last column
    if(col == (ccl - 1)) or (lin == (ccl - 1)):
        #tots and percents
        if(cell_val != 0):
            if(col == ccl - 1) and (lin == ccl - 1):
                tot_rig = 0
                for i in range(array_df.shape[0] - 1):
                    tot_rig += array_df[i][i]
                per_ok = (float(tot_rig) / cell_val) * 100
            elif(col == ccl - 1):
                tot_rig = array_df[lin][lin]
                per_ok = (float(tot_rig) / cell_val) * 100
            elif(lin == ccl - 1):
                tot_rig = array_df[col][col]
                per_ok = (float(tot_rig) / cell_val) * 100
            per_err = 100 - per_ok
        else:
            per_ok = per_err = 0

        per_ok_s = ['%.1f%%'%(per_ok), '100%'] [per_ok == 100]

        #text to DEL
        text_del.append(oText)

        #text to ADD
        font_prop = fm.FontProperties(weight='bold', size=fz)
        text_kwargs = dict(color='w', ha="center", va="center", gid='sum', fontproperties=font_prop)
        lis_txt = ['%d'%(cell_val), per_ok_s, '%.1f%%'%(per_err)]
        lis_kwa = [text_kwargs]
        dic = text_kwargs.copy(); dic['color'] = 'g'; lis_kwa.append(dic);
        dic = text_kwargs.copy(); dic['color'] = 'r'; lis_kwa.append(dic);
        lis_pos = [(oText._x, oText._y-0.3), (oText._x, oText._y), (oText._x, oText._y+0.3)]
        for i in range(len(lis_txt)):
            newText = dict(x=lis_pos[i][0], y=lis_pos[i][1], text=lis_txt[i], kw=lis_kwa[i])
            #print 'lin: %s, col: %s, newText: %s' %(lin, col, newText)
            text_add.append(newText)
        #print '\n'

        #set background color for sum cells (last line and last column)
        carr = [0.27, 0.30, 0.27, 1.0]
        if(col == ccl - 1) and (lin == ccl - 1):
            carr = [0.17, 0.20, 0.17, 1.0]
        facecolors[posi] = carr

    else:
        if(per > 0):
            txt = '%s\n%.1f%%' %(cell_val, per)
        else:
            if(show_null_values == 0):
                txt = ''
            elif(show_null_values == 1):
                txt = '0'
            else:
                txt = '0\n0.0%'
        oText.set_text(txt)

        #main diagonal
        if(col == lin):
            #set color of the textin the diagonal to white
            oText.set_color('w')
            # set background color in the diagonal to blue
            facecolors[posi] = [0.35, 0.8, 0.55, 1.0]
        else:
            oText.set_color('r')

    return text_add, text_del
#

def insert_totals(df_cm):
    """ insert total column and line (the last ones) """
    sum_col = []
    for c in df_cm.columns:
        sum_col.append( df_cm[c].sum() )
    sum_lin = []
    for item_line in df_cm.iterrows():
        sum_lin.append( item_line[1].sum() )
    df_cm['sum_lin'] = sum_lin
    sum_col.append(np.sum(sum_lin))
    df_cm.loc['sum_col'] = sum_col
    #print ('\ndf_cm:\n', df_cm, '\n\b\n')
#

def pretty_plot_confusion_matrix(df_cm, annot=True, cmap="Oranges", fmt='.2f', fz=11,
      lw=0.5, cbar=False, figsize=[8,8], show_null_values=0, pred_val_axis='y'):
    """
      print conf matrix with default layout (like matlab)
      params:
        df_cm          dataframe (pandas) without totals
        annot          print text in each cell
        cmap           Oranges,Oranges_r,YlGnBu,Blues,RdBu, ... see:
        fz             fontsize
        lw             linewidth
        pred_val_axis  where to show the prediction values (x or y axis)
                        'col' or 'x': show predicted values in columns (x axis) instead lines
                        'lin' or 'y': show predicted values in lines   (y axis)
    """
    if(pred_val_axis in ('col', 'x')):
        xlbl = 'Predicted'
        ylbl = 'Actual'
    else:
        xlbl = 'Actual'
        ylbl = 'Predicted'
        df_cm = df_cm.T

    # create "Total" column
    insert_totals(df_cm)

    #this is for print allways in the same window
    fig, ax1 = get_new_fig('Conf matrix default', figsize)

    #thanks for seaborn
    ax = sn.heatmap(df_cm, annot=annot, annot_kws={"size": fz}, linewidths=lw, ax=ax1,
                    cbar=cbar, cmap=cmap, linecolor='w', fmt=fmt)

    #set ticklabels rotation
    ax.set_xticklabels(ax.get_xticklabels(), rotation = 45, fontsize = 10)
    ax.set_yticklabels(ax.get_yticklabels(), rotation = 25, fontsize = 10)

    # Turn off all the ticks
    for t in ax.xaxis.get_major_ticks():
        t.tick1On = False
        t.tick2On = False
    for t in ax.yaxis.get_major_ticks():
        t.tick1On = False
        t.tick2On = False

    #face colors list
    quadmesh = ax.findobj(QuadMesh)[0]
    facecolors = quadmesh.get_facecolors()

    #iter in text elements
    array_df = np.array( df_cm.to_records(index=False).tolist() )
    text_add = []; text_del = [];
    posi = -1 #from left to right, bottom to top.
    for t in ax.collections[0].axes.texts: #ax.texts:
        pos = np.array( t.get_position()) - [0.5,0.5]
        lin = int(pos[1]); col = int(pos[0]);
        posi += 1
        #print ('>>> pos: %s, posi: %s, val: %s, txt: %s' %(pos, posi, array_df[lin][col], t.get_text()))

        #set text
        txt_res = configcell_text_and_colors(array_df, lin, col, t, facecolors, posi, fz, fmt, show_null_values)

        text_add.extend(txt_res[0])
        text_del.extend(txt_res[1])

    #remove the old ones
    for item in text_del:
        item.remove()
    #append the new ones
    for item in text_add:
        ax.text(item['x'], item['y'], item['text'], **item['kw'])

    #titles and legends
    ax.set_title('Confusion matrix')
    ax.set_xlabel(xlbl)
    ax.set_ylabel(ylbl)
    plt.tight_layout()  #set layout slim
    plt.show()
    return fig
#

def plot_confusion_matrix_from_data(y_test, predictions, columns=None, annot=True, cmap="Oranges",
      fmt='.2f', fz=11, lw=0.5, cbar=False, figsize=[8,8], show_null_values=0, pred_val_axis='lin'):
    """
        plot confusion matrix function with y_test (actual values) and predictions (predic),
        whitout a confusion matrix yet
    """
    from sklearn.metrics import confusion_matrix
    from pandas import DataFrame

    #data
    if(not columns):
        #labels axis integer:
        ##columns = range(1, len(np.unique(y_test))+1)
        #labels axis string:
        from string import ascii_uppercase
        columns = ['class %s' %(i) for i in list(ascii_uppercase)[0:len(np.unique(y_test))]]

    confm = confusion_matrix(y_test, predictions)
    cmap = 'Oranges';
    fz = 11;
    figsize=[9,9];
    show_null_values = 2
    df_cm = DataFrame(confm, index=columns, columns=columns)
    pretty_plot_confusion_matrix(df_cm, fz=fz, cmap=cmap, figsize=figsize, show_null_values=show_null_values, pred_val_axis=pred_val_axis)
#



#
#TEST functions
#
def _test_cm():
    #test function with confusion matrix done
    array = np.array( [[13,  0,  1,  0,  2,  0],
                       [ 0, 50,  2,  0, 10,  0],
                       [ 0, 13, 16,  0,  0,  3],
                       [ 0,  0,  0, 13,  1,  0],
                       [ 0, 40,  0,  1, 15,  0],
                       [ 0,  0,  0,  0,  0, 20]])
    #get pandas dataframe
    df_cm = DataFrame(array, index=range(1,7), columns=range(1,7))
    #colormap: see this and choose your more dear
    cmap = 'PuRd'
    pretty_plot_confusion_matrix(df_cm, cmap=cmap)
#

def _test_data_class():
    """ test function with y_test (actual values) and predictions (predic) """
    #data
    y_test = np.array([1,2,3,4,5, 1,2,3,4,5, 1,2,3,4,5, 1,2,3,4,5, 1,2,3,4,5, 1,2,3,4,5, 1,2,3,4,5, 1,2,3,4,5, 1,2,3,4,5, 1,2,3,4,5, 1,2,3,4,5, 1,2,3,4,5, 1,2,3,4,5, 1,2,3,4,5, 1,2,3,4,5, 1,2,3,4,5, 1,2,3,4,5, 1,2,3,4,5, 1,2,3,4,5, 1,2,3,4,5, 1,2,3,4,5, 1,2,3,4,5])
    predic = np.array([1,2,4,3,5, 1,2,4,3,5, 1,2,3,4,4, 1,4,3,4,5, 1,2,4,4,5, 1,2,4,4,5, 1,2,4,4,5, 1,2,4,4,5, 1,2,3,3,5, 1,2,3,3,5, 1,2,3,4,4, 1,2,3,4,1, 1,2,3,4,1, 1,2,3,4,1, 1,2,4,4,5, 1,2,4,4,5, 1,2,4,4,5, 1,2,4,4,5, 1,2,3,4,5, 1,2,3,4,5, 1,2,3,4,5, 1,2,3,4,5])
    """
      Examples to validate output (confusion matrix plot)
        actual: 5 and prediction 1   >>  3
        actual: 2 and prediction 4   >>  1
        actual: 3 and prediction 4   >>  10
    """
    columns = []
    annot = True;
    cmap = 'Oranges';
    fmt = '.2f'
    lw = 0.5
    cbar = False
    show_null_values = 2
    pred_val_axis = 'y'
    #size::
    fz = 12;
    figsize = [9,9];
    if(len(y_test) > 10):
        fz=9; figsize=[14,14];
    plot_confusion_matrix_from_data(y_test, predic, columns,
      annot, cmap, fmt, fz, lw, cbar, figsize, show_null_values, pred_val_axis)

In [ ]:
# plot_confusion_matrix_from_data(y_test, predictions, columns=None, annot=True, cmap="Oranges",
#       fmt='.2f', fz=11, lw=0.5, cbar=False, figsize=[8,8], show_null_values=0, pred_val_axis='lin'):

matplotlib.rcParams['text.usetex'] = False

forecast_model = 'postintertidal_slope_sto06'

df_for = impacts['forecasted'][forecast_model]
df_for.storm_regime = df_for.storm_regime.astype(cat_type)
observed_regimes = df_obs.storm_regime.astype(cat_type).cat.codes.values
forecasted_regimes = df_for.storm_regime.astype(cat_type).cat.codes.values


confm = confusion_matrix(observed_regimes, forecasted_regimes,labels=[0,1,2,3])
labels=['swash','collision','overwash','inundation']
df_cm = DataFrame(confm, index=labels, columns=labels)

fig = pretty_plot_confusion_matrix(df_cm, annot=True, cmap="Oranges", fmt='.1f', fz=13,
      lw=0.1, cbar=False, figsize=[8,5], show_null_values=1, pred_val_axis='y')

fig.savefig('11_confusion_matrix',dpi=600)